#1. 라이브러리 임포트

In [ ]:
! pip install albumentations==0.4.6

     |████████████████████████████████| 122kB 9.0MB/s 
     |████████████████████████████████| 952kB 13.0MB/s 
  Created wheel for albumentations: filename=albumentations-0.4.6-cp37-none-any.whl size=65163 sha256=7ffc2e1208c000d83f09684344da68105e4628a14eb1c5ee27508af3856ef9d7
  Stored in directory: /root/.cache/pip/wheels/c7/f4/89/56d1bee5c421c36c1a951eeb4adcc32fbb82f5344c086efa14
Successfully built albumentations
  Found existing installation: imgaug 0.2.9
    Uninstalling imgaug-0.2.9:
      Successfully uninstalled imgaug-0.2.9
  Found existing installation: albumentations 0.1.12
    Uninstalling albumentations-0.1.12:
      Successfully uninstalled albumentations-0.1.12


In [ ]:
import torch
print(torch.__version__)
import torchvision
print(torchvision.__version__)
import torch.nn as nn
import torch.optim as optim
import torchvision.transforms as transforms
from torch import Tensor
from torch.utils.data import DataLoader, Dataset
import torch.nn.functional as F
from torchvision.models.detection.backbone_utils import resnet_fpn_backbone
from torchvision.ops import MultiScaleRoIAlign
from torchvision.models.detection import KeypointRCNN
import matplotlib.pyplot as plt
import gc
import cv2
import numpy as np
import os
import pandas as pd
import albumentations as A
from albumentations.pytorch import ToTensorV2
from tqdm.notebook import tqdm
from typing import Tuple, List, Sequence, Callable, Dict
from torch.utils.tensorboard import SummaryWriter #tensorboard

1.8.0
0.9.0


In [ ]:
import subprocess

def get_gpu_memory_map():
    """Get the current gpu usage.

    Returns
    -------
    usage: dict
        Keys are device ids as integers.
        Values are memory usage as integers in MB.
    """
    result = subprocess.check_output(
        [
            'nvidia-smi', '--query-gpu=memory.used',
            '--format=csv,nounits,noheader'
        ], encoding='utf-8')
    # Convert lines into a dictionary
    gpu_memory = [int(x) for x in result.strip().split('\n')]
    gpu_memory_map = dict(zip(range(len(gpu_memory)), gpu_memory))
    return gpu_memory_map

#gpu 메모리 확인
print(f'gpu 사용량 : {get_gpu_memory_map()}')

gpu 사용량 : {0: 369}


In [ ]:
gc.collect()
torch.cuda.empty_cache()

In [ ]:
device = 'cuda:0' if torch.cuda.is_available() else 'cpu'
print(device)

cuda:0


# 2. 코랩 연결 부분

In [ ]:
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

ModuleNotFoundError: No module named 'google.colab'

In [ ]:
#root_dir = '/content/drive/MyDrive/'
root_dir = '/home/jngeun/motion_keypoint'

In [ ]:
feature_extracting= False
num_classes = 48
learning_rate = 1e-4
batch_size = 2
num_epochs = 1000
test_dir = 'data/test_imgs'
train_dir = "data/train_imgs"
train_df_csv = "data/train_df.csv"
test_imgs = os.listdir(os.path.join(root_dir,test_dir))

# 3. 함수 정의 부분

In [ ]:
def collate_fn(batch):
    return tuple(zip(*batch))

In [ ]:
def get_model() -> nn.Module:
    backbone = resnet_fpn_backbone('resnet101', pretrained=True)
    roi_pooler = MultiScaleRoIAlign(
        featmap_names=['0', '1', '2', '3'],
        output_size=7,
        sampling_ratio=2
    )

    keypoint_roi_pooler = MultiScaleRoIAlign(
        featmap_names=['0', '1', '2', '3'],
        output_size=14,
        sampling_ratio=2
    )

    model = KeypointRCNN(
        backbone, 
        num_classes=2,
        num_keypoints=24,
        box_roi_pool=roi_pooler,
        keypoint_roi_pool=keypoint_roi_pooler
    )

    return model

In [ ]:
def set_parameter_requires_grad(model,feature_extracting):
  if feature_extracting:
    for param in model.backbone.parameters():
      param.requires_grad = False
      # False로 바뀐 부분을 학습 안하겠다.


## image processing

In [ ]:
def gaussian_filter(kernel_shape):
    x = np.zeros(kernel_shape, dtype='float32')
 
    def gauss(x, y, sigma=2.0):
        Z = 2 * np.pi * sigma ** 2
        return  1. / Z * np.exp(-(x ** 2 + y ** 2) / (2. * sigma ** 2))
 
    mid = np.floor(kernel_shape[-1] / 2.)
    for kernel_idx in range(0, kernel_shape[1]):
        for i in range(0, kernel_shape[2]):
            for j in range(0, kernel_shape[3]):
                x[0, kernel_idx, i, j] = gauss(i - mid, j - mid)
 
    return x / np.sum(x)

In [ ]:
def LocalContrastNorm(image,radius=9):
    """
    image: torch.Tensor , .shape => (1,channels,height,width) 
    
    radius: Gaussian filter size (int), odd
    """
    

    if radius%2 == 0:
        radius += 1
    def get_gaussian_filter(kernel_shape):
        x = np.zeros(kernel_shape, dtype='float64')
 
        def gauss(x, y, sigma=2.0):
            Z = 2 * np.pi * sigma ** 2
            return  1. / Z * np.exp(-(x ** 2 + y ** 2) / (2. * sigma ** 2))
 
        mid = np.floor(kernel_shape[-1] / 2.)
        for kernel_idx in range(0, kernel_shape[1]):
            for i in range(0, kernel_shape[2]):
                for j in range(0, kernel_shape[3]):
                    x[0, kernel_idx, i, j] = gauss(i - mid, j - mid)
 
        return x / np.sum(x)
    
    n,c,h,w = image.shape[0],image.shape[1],image.shape[2],image.shape[3]

    gaussian_filter = torch.Tensor(get_gaussian_filter((1,c,radius,radius))).double()
    filtered_out = F.conv2d(image,gaussian_filter,padding=radius-1)
    mid = int(np.floor(gaussian_filter.shape[2] / 2.))
    ### Subtractive Normalization
    centered_image = image - filtered_out[:,:,mid:-mid,mid:-mid]
    
    ## Variance Calc
    sum_sqr_image = F.conv2d(centered_image.pow(2),gaussian_filter,padding=radius-1)
    s_deviation = sum_sqr_image[:,:,mid:-mid,mid:-mid].sqrt()
    #gfilter = torch.Tensor(gaussian_filter((1,3,9,9))).double()
    #filtered = F.conv2d(image_tensor,gfilter,padding=8) ## padding = 8 = 9-1 (radius - 1 ) for border == 'full'
    sum_sqr_XX = F.conv2d(centered_image.pow(2),gaussian_filter,padding=8)
    denom = sum_sqr_XX[:,:,mid:-mid,mid:-mid].sqrt()
    per_img_mean = denom.mean()
    
    ## Divisive Normalization
    divisor = np.maximum(per_img_mean.numpy(),s_deviation.numpy())
    divisor = np.maximum(divisor, 1e-4)
    new_image = centered_image / torch.Tensor(divisor)
    return new_image



## Data augmentation

## checkout augmented image

In [ ]:
def draw_keypoints(
    image: np.ndarray,
    keypoints: np.ndarray,
    edges: List[Tuple[int, int]] = None,
    keypoint_names: Dict[int, str] = None, 
    boxes: bool = True
) -> np.ndarray:
    """
    Args:
        image (ndarray): [H, W, C]
        keypoints (ndarray): [N, 3]
        edges (List(Tuple(int, int))): 
    """
    np.random.seed(42)
    colors = {k: tuple(map(int, np.random.randint(0, 255, 3))) for k in range(24)}

    if boxes:
        x1, y1 = min(keypoints[:, 0]), min(keypoints[:, 1])
        x2, y2 = max(keypoints[:, 0]), max(keypoints[:, 1])
        cv2.rectangle(image, (x1, y1), (x2, y2), (255, 100, 91), thickness=3)

    for i, keypoint in enumerate(keypoints):
        cv2.circle(
            image, 
            tuple(keypoint), 
            3, colors.get(i), thickness=1, lineType=cv2.FILLED)

        if keypoint_names is not None:
            cv2.putText(
                image, 
                f'{i}: {keypoint_names[i]}', 
                tuple(keypoint), 
                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 0), 1)

    if edges is not None:
        for i, edge in enumerate(edges):
            cv2.line(
                image, 
                tuple(keypoints[edge[0]]), 
                tuple(keypoints[edge[1]]),
                colors.get(edge[0]), 1, lineType=cv2.LINE_AA)
    return image
    

In [ ]:
def checkout_trn_img(idx : int):
    img, targets = train_data.__getitem__(idx)
        
    
    img = np.array(img)
    keypoints = np.array(targets['keypoints'][:,:,:2]).reshape(-1, 2)
    keypoints = keypoints.astype(np.int64)
    
    keypoint_names = {
        0: 'nose',
        1: 'left_eye',
        2: 'right_eye',
        3: 'left_ear', 
        4: 'right_ear', 
        5: 'left_shoulder', 
        6: 'right_shoulder',
        7: 'left_elbow', 
        8: 'right_elbow',
        9: 'left_wrist', 
        10: 'right_wrist',
        11: 'left_hip', 
        12: 'right_hip',
        13: 'left_knee', 
        14: 'right_knee',
        15: 'left_ankle', 
        16: 'right_ankle',
        17: 'neck', 
        18: 'left_palm', 
        19: 'right_palm', 
        20: 'spine2(back)',
        21: 'spine1(waist)', 
        22: 'left_instep',
        23: 'right_instep'
    }

    edges = [
        (0, 1), (0, 2), (2, 4), (1, 3), (6, 8), (8, 10), (9, 18),
        (10, 19), (5, 7), (7, 9), (11, 13), (13, 15), (12, 14),
        (14, 16), (15, 22), (16, 23), (20, 21), (5, 6), (5, 11),
        (6, 12), (11, 12), (17, 20), (20, 21), 
    ]
    img = np.transpose(img,(0,1,2))
    
    img =  draw_keypoints(img, keypoints,edges, keypoint_names, boxes=False)
  
    return img

In [ ]:
def checkout_pred(idx : int,predictions):
    filename, img = test_data.__getitem__(idx)
    keypoints = predictions[idx].reshape(-1,2)
    keypoints = keypoints.astype(np.int64)
    
    img = np.array(img)
    keypoint_names = {
        0: 'nose',
        1: 'left_eye',
        2: 'right_eye',
        3: 'left_ear', 
        4: 'right_ear', 
        5: 'left_shoulder', 
        6: 'right_shoulder',
        7: 'left_elbow', 
        8: 'right_elbow',
        9: 'left_wrist', 
        10: 'right_wrist',
        11: 'left_hip', 
        12: 'right_hip',
        13: 'left_knee', 
        14: 'right_knee',
        15: 'left_ankle', 
        16: 'right_ankle',
        17: 'neck', 
        18: 'left_palm', 
        19: 'right_palm', 
        20: 'spine2(back)',
        21: 'spine1(waist)', 
        22: 'left_instep',
        23: 'right_instep'
    }

    edges = [
        (0, 1), (0, 2), (2, 4), (1, 3), (6, 8), (8, 10), (9, 18),
        (10, 19), (5, 7), (7, 9), (11, 13), (13, 15), (12, 14),
        (14, 16), (15, 22), (16, 23), (20, 21), (5, 6), (5, 11),
        (6, 12), (11, 12), (17, 20), (20, 21), 
    ]
    img = np.transpose(img,(1,2,0))
    img =  draw_keypoints(img, keypoints,edges, keypoint_names, boxes=False)
  
    fig, ax = plt.subplots(figsize=(300, 200))
    ax.imshow(img)
    ax.axis('off')
    plt.title(filename)
    plt.show()

# 데이터 로드

## class 정의

In [ ]:
# augmentation 
A_transforms = {
    'train':
        A.Compose([
            #A.Resize(224, 224, always_apply=True),
            A.Rotate(limit=40,p=0),
            A.OneOf([A.HorizontalFlip(p=1),
                     A.RandomRotate90(p=1),
                     A.VerticalFlip(p=1)            
            ], p=0),
            A.OneOf([A.MotionBlur(p=1),
                     A.GaussNoise(p=1)                 
            ], p=0),
            #A.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225]),
            ToTensorV2()
        ],  bbox_params=A.BboxParams(format='pascal_voc', label_fields=['labels']),
            keypoint_params=A.KeypointParams(format='xy')) ,
    
    'val':
        A.Compose([
            #A.Resize(224, 224, always_apply=True),
            #A.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225]),
            ToTensorV2()
        ], bbox_params=A.BboxParams(format='pascal_voc', label_fields=['labels']),
            keypoint_params=A.KeypointParams(format='xy')),
    
    'test':
        A.Compose([
            #A.Resize(224, 224, always_apply=True),
          
          #  A.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225]),
            ToTensorV2()
        ])
}

In [ ]:
class KeypointDataset(Dataset):
    def __init__(self, data_dir, label_path, phase=None, transforms=None):
        self.data_dir = data_dir
        self.df = pd.read_csv(label_path)
        self.transforms = transforms
        self.phase= phase
    def __len__(self) -> int:
        return self.df.shape[0]
    
    def __getitem__(self, index) -> Tuple[Tensor, Dict]:
        image_id = self.df.iloc[index, 0]
        labels = np.array([1])
        keypoints = self.df.iloc[index, 1:].values.reshape(-1, 2).astype(np.int64)

        x1, y1 = min(keypoints[:, 0]), min(keypoints[:, 1])
        x2, y2 = max(keypoints[:, 0]), max(keypoints[:, 1])
        boxes = np.array([[x1, y1, x2, y2]], dtype=np.int64)

        image = cv2.imread(os.path.join(self.data_dir, image_id), cv2.COLOR_BGR2RGB)

        targets ={
            'image': image,
            'bboxes': boxes,
            'labels': labels,
            'keypoints': keypoints
        }

        if self.transforms is not None:
          targets = self.transforms[self.phase](**targets)
        
        image = targets['image']
        image = image / 255.0

        targets = {
            'labels': torch.as_tensor(targets['labels'], dtype=torch.int64),
            'boxes': torch.as_tensor(targets['bboxes'], dtype=torch.float32),
            'keypoints': torch.as_tensor(
                np.concatenate([targets['keypoints'], np.ones((24, 1))], axis=1)[np.newaxis], dtype=torch.float32
            )
        }

        return image, targets

In [ ]:
class TestDataset(Dataset):
    """__init__ and __len__ functions are the same as in TorchvisionDataset"""
    def __init__(self, data_dir, imgs, phase, transforms=None):
        self.data_dir = data_dir
        self.imgs = imgs
        self.phase = phase
        self.transforms = transforms

    def __getitem__(self, idx):
        filename = self.imgs[idx]
        # Read an image with OpenCV
        img = cv2.imread(os.path.join(self.data_dir, self.imgs[idx]))

        if self.transforms:
            augmented = self.transforms[self.phase](image=img)
            img = augmented['image'].float()
            img = img / 255.

#         #LCN
#         img = torch.tensor([np.array(img)])
#         img = LocalContrastNorm(img,radius=9)[0]
#         img = ((img - torch.min(img))/(torch.max(img) - torch.min(img))).float() #image를 0~1로 고정

        return filename, img
    
    def __len__(self):
        return len(self.imgs)
  


In [ ]:
# train dataset augmentation 을 위한 maping class
class MapTrainDataset(Dataset): 
    """
    Given a dataset, creates a dataset which applies a mapping function
    to its items (lazily, only when an item is called).

    Note that data is not cloned/copied from the initial dataset.
    """

    def __init__(self, dataset):
        self.dataset = dataset


    def __getitem__(self, index):
      targets ={
            'image': self.dataset[index][0],
            'bboxes': self.dataset[index][1]['boxes'],
            'labels': self.dataset[index][1]['labels'],
            'keypoints': self.dataset[index][1]['keypoints'][0][:,:2]
        }
      targets = A_transforms['train'](**targets)  
      image =targets['image']
      
#       #LCN
#       image = torch.tensor([np.array(image)])
#       image = LocalContrastNorm(image,radius=9)[0]
#       image = ((image - torch.min(image))/(torch.max(image) - torch.min(image))) #image를 0~1로 고정

      targets = {
            'labels': torch.as_tensor(targets['labels'], dtype=torch.int64),
            'boxes': torch.as_tensor(targets['bboxes'], dtype=torch.float32),
            'keypoints': torch.as_tensor(
                np.concatenate([targets['keypoints'], np.ones((24, 1))], axis=1)[np.newaxis], dtype=torch.float32
            )
        }
      return image, targets
    def __len__(self):
        return len(self.dataset)


In [ ]:
# valid dataset augmentation 을 위한 maping class
class MapValidDataset(Dataset):
    """
    Given a dataset, creates a dataset which applies a mapping function
    to its items (lazily, only when an item is called).

    Note that data is not cloned/copied from the initial dataset.
    """

    def __init__(self, dataset):
        self.dataset = dataset

    def __getitem__(self, index):
      targets ={
            'image': self.dataset[index][0],
            'bboxes': self.dataset[index][1]['boxes'],
            'labels': self.dataset[index][1]['labels'],
            'keypoints': self.dataset[index][1]['keypoints'][0][:,:2]
        }
      targets = A_transforms['val'](**targets)  
      image =targets['image']

#       #LCN
#       image = torch.tensor([np.array(image)])
#       image = LocalContrastNorm(image,radius=9)[0]
#       image = (image - torch.min(image))/(torch.max(image) - torch.min(image)) #image를 0~1로 고정

      targets = {
            'labels': torch.as_tensor(targets['labels'], dtype=torch.int64),
            'boxes': torch.as_tensor(targets['bboxes'], dtype=torch.float32),
            'keypoints': torch.as_tensor(
                np.concatenate([targets['keypoints'], np.ones((24, 1))], axis=1)[np.newaxis], dtype=torch.float32
            )
        }
      return image, targets
    def __len__(self):
        return len(self.dataset)


In [ ]:
np.random.seed(42)
# 항상 동일한 valid set을 설정

train_data = KeypointDataset(data_dir = os.path.join(root_dir,train_dir),label_path = os.path.join(root_dir,train_df_csv))
test_data = TestDataset(data_dir=os.path.join(root_dir,test_dir), imgs=test_imgs,transforms=A_transforms,  phase='test')

num_train = len(train_data)
indices = list(range(num_train))
np.random.shuffle(indices)
split = int(np.floor(0.1 * num_train))

train_idx, valid_idx = indices[split:], indices[:split]

tng_data = torch.utils.data.Subset(train_data, train_idx)
val_data = torch.utils.data.Subset(train_data, valid_idx)

# maping for augmentation
tng_data_tf = MapTrainDataset(tng_data)
val_data_tf = MapValidDataset(val_data)

# data load
train_loader = DataLoader(tng_data_tf, batch_size=batch_size,collate_fn=collate_fn)
val_loader = DataLoader(val_data_tf, batch_size=batch_size,collate_fn=collate_fn)
test_loader = DataLoader(test_data,batch_size=batch_size,shuffle=False)

## Local Contrast Normalization
이론링크 : https://deepestdocs.readthedocs.io/en/latest/003_image_processing/0030/  
코드링크 : https://github.com/dibyadas/Visualize-Normalizations/blob/master/LocalContrastNorm.ipynb

# 4. 모델 초기화

In [ ]:
model = get_model()
model.cuda()
set_parameter_requires_grad(model,feature_extracting)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(),lr=learning_rate)
#optimizer = optim.SGD(model.parameters(), lr=1e-4, momentum=0.9, weight_decay=5e-4)
#patience만큼 loss가 향상되지 않으면 learning_rate에 factor을 곱해줌 
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer,factor = 0.1, patience = 5, verbose=True)
writer = SummaryWriter()

In [ ]:
#gpu 메모리 확인
print(get_gpu_memory_map())

{0: 1543}


## 4.1 모델 로드

In [ ]:
model = get_model()

criterion = nn.CrossEntropyLoss()
#optimizer = optim.Adam(model.parameters(),lr=learning_rate)
optimizer = optim.SGD(model.parameters(), lr=1e-4, momentum=0.9, weight_decay=5e-4)
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer,factor = 0.1, patience = 5, verbose=True)
checkpoint = torch.load(os.path.join(root_dir,'model_40.pt'))
model.load_state_dict(checkpoint['model_state_dict'])
optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
epoch = checkpoint['epoch']
loss = checkpoint['loss']
model.cuda()

KeypointRCNN(
  (transform): GeneralizedRCNNTransform(
      Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
      Resize(min_size=(640, 672, 704, 736, 768, 800), max_size=1333, mode='bilinear')
  )
  (backbone): BackboneWithFPN(
    (body): IntermediateLayerGetter(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): FrozenBatchNorm2d(64, eps=1e-05)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): FrozenBatchNorm2d(64, eps=1e-05)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): FrozenBatchNorm2d(64, eps=1e-05)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): FrozenBatchNorm2d(256, 

# 5. train / save

In [ ]:
min_loss = 9999

early_stopping_idx = 0;
for epoch in range(num_epochs):
    model.train()
    cal_loss = []
    loss_for_validation = []
    losses = []
    loop = tqdm(train_loader)
    for i, (images, targets) in enumerate(loop):
        #grad init
        optimizer.zero_grad()
        #forward propagation
        images = list(image.float().to(device) for image in images)
        #target
        targets = [{k: v.to(device) for k, v in t.items()} for t in targets]
        #calculate loss
        losses = model(images,targets)
        loss = sum(loss for loss in losses.values())
        cal_loss.append(loss)
        #back propagation
        loss.backward()
        #weight update
        optimizer.step() 
        
        if (i+1) % 10 == 0:
            print(f'| epoch: {epoch} | loss: {loss.item():.4f}')
            print()
        
    # validation
    with torch.no_grad():
        for k, (val_images, val_targets) in enumerate(val_loader):
            val_images = list(val_image.float().to(device) for val_image in val_images)
            val_targets = [{k: v.to(device) for k, v in t.items()} for t in val_targets]
            val_losses = model(val_images,val_targets)
            val_loss = sum(loss for loss in val_losses.values())
            loss_for_validation.append(val_loss)


    mean_val_loss = sum(loss_for_validation) / len(loss_for_validation)
    mean_loss = sum(cal_loss) / len(cal_loss)
    lr = optimizer.param_groups[0]['lr']
    scheduler.step(mean_loss)
    writer.add_scalar("Loss/val", mean_val_loss,epoch)
    writer.add_scalar("Loss/train", mean_loss, epoch)
    writer.add_scalar("learning_rate", lr, epoch)
    print(f'| epoch: {epoch} | loss: {mean_loss:.4f} | lr : {lr} | validation loss : {mean_val_loss:.4f}')
    print()
    
    if epoch % 10 == 0:
        torch.save({
              'epoch': epoch,
              'model_state_dict': model.state_dict(),
              'optimizer_state_dict': optimizer.state_dict(),
              'loss': loss}
              ,os.path.join(root_dir,f'model_{epoch}.pt'))
    
    if mean_val_loss < min_loss:
      early_stopping_idx = 0
      min_loss = mean_val_loss
      torch.save({
              'epoch': epoch,
              'model_state_dict': model.state_dict(),
              'optimizer_state_dict': optimizer.state_dict(),
              'loss': loss}
              ,os.path.join(root_dir,'best_model.pt'))
    else:
        print("Val_loss_increase")
        early_stopping_idx +=1
        if early_stopping_idx == 10:
        print("early stop")
        #break
writer.flush()

  0%|          | 0/1888 [00:00<?, ?it/s]

| epoch: 0 | loss: 7.8069

| epoch: 0 | loss: 7.4859

| epoch: 0 | loss: 7.7458

| epoch: 0 | loss: 7.2671

| epoch: 0 | loss: 8.1925

| epoch: 0 | loss: 6.9249

| epoch: 0 | loss: 6.7209

| epoch: 0 | loss: 6.6958

| epoch: 0 | loss: 7.4973

| epoch: 0 | loss: 7.2810

| epoch: 0 | loss: 6.9966

| epoch: 0 | loss: 7.1981

| epoch: 0 | loss: 6.7090

| epoch: 0 | loss: 7.3461

| epoch: 0 | loss: 6.5038

| epoch: 0 | loss: 6.3795

| epoch: 0 | loss: 5.8982

| epoch: 0 | loss: 5.7828

| epoch: 0 | loss: 6.1704

| epoch: 0 | loss: 6.9371

| epoch: 0 | loss: 6.2356

| epoch: 0 | loss: 7.1994

| epoch: 0 | loss: 6.6305

| epoch: 0 | loss: 6.2580

| epoch: 0 | loss: 6.6634

| epoch: 0 | loss: 6.1614

| epoch: 0 | loss: 6.1985

| epoch: 0 | loss: 5.5244

| epoch: 0 | loss: 7.1861

| epoch: 0 | loss: 5.7157

| epoch: 0 | loss: 6.1139

| epoch: 0 | loss: 4.9987

| epoch: 0 | loss: 5.3602

| epoch: 0 | loss: 4.9307

| epoch: 0 | loss: 5.1300

| epoch: 0 | loss: 5.0700

| epoch: 0 | loss: 5.5524

|

  0%|          | 0/1888 [00:00<?, ?it/s]

| epoch: 1 | loss: 3.8457

| epoch: 1 | loss: 3.3778

| epoch: 1 | loss: 3.2693

| epoch: 1 | loss: 3.0465

| epoch: 1 | loss: 5.4112

| epoch: 1 | loss: 3.7893

| epoch: 1 | loss: 3.5203

| epoch: 1 | loss: 3.3297

| epoch: 1 | loss: 4.2371

| epoch: 1 | loss: 4.0885

| epoch: 1 | loss: 3.4548

| epoch: 1 | loss: 3.6705

| epoch: 1 | loss: 3.8563

| epoch: 1 | loss: 3.8409

| epoch: 1 | loss: 3.6766

| epoch: 1 | loss: 4.0135

| epoch: 1 | loss: 3.6789

| epoch: 1 | loss: 3.9039

| epoch: 1 | loss: 3.2728

| epoch: 1 | loss: 4.2204

| epoch: 1 | loss: 3.3948

| epoch: 1 | loss: 3.6699

| epoch: 1 | loss: 3.9563

| epoch: 1 | loss: 3.7823

| epoch: 1 | loss: 3.7976

| epoch: 1 | loss: 3.4269

| epoch: 1 | loss: 4.2832

| epoch: 1 | loss: 2.6935

| epoch: 1 | loss: 5.4033

| epoch: 1 | loss: 3.4690

| epoch: 1 | loss: 3.3324

| epoch: 1 | loss: 3.3062

| epoch: 1 | loss: 3.4056

| epoch: 1 | loss: 2.6073

| epoch: 1 | loss: 2.8322

| epoch: 1 | loss: 3.3753

| epoch: 1 | loss: 3.2628

|

  0%|          | 0/1888 [00:00<?, ?it/s]

...

  0%|          | 0/1888 [00:00<?, ?it/s]

| epoch: 78 | loss: 0.9219

| epoch: 78 | loss: 1.0799

| epoch: 78 | loss: 1.3469

| epoch: 78 | loss: 1.3450

| epoch: 78 | loss: 1.0225

| epoch: 78 | loss: 1.3650

| epoch: 78 | loss: 1.2520

| epoch: 78 | loss: 1.2100

| epoch: 78 | loss: 1.3594

| epoch: 78 | loss: 1.0202

| epoch: 78 | loss: 1.2516

| epoch: 78 | loss: 0.9300

| epoch: 78 | loss: 1.1051

| epoch: 78 | loss: 1.2449

| epoch: 78 | loss: 1.1430

| epoch: 78 | loss: 1.3811

| epoch: 78 | loss: 1.2103

| epoch: 78 | loss: 1.1982

| epoch: 78 | loss: 1.1698

| epoch: 78 | loss: 1.3158

| epoch: 78 | loss: 1.1362

| epoch: 78 | loss: 1.7223

| epoch: 78 | loss: 1.3994

| epoch: 78 | loss: 1.0699

| epoch: 78 | loss: 1.1627

| epoch: 78 | loss: 1.1166

| epoch: 78 | loss: 0.9167

| epoch: 78 | loss: 0.9549

| epoch: 78 | loss: 1.1141

| epoch: 78 | loss: 1.4362

| epoch: 78 | loss: 1.0423

| epoch: 78 | loss: 1.2801

| epoch: 78 | loss: 1.3360

| epoch: 78 | loss: 1.0165

| epoch: 78 | loss: 1.1895

| epoch: 78 | loss: 

  0%|          | 0/1888 [00:00<?, ?it/s]

| epoch: 79 | loss: 1.0767

| epoch: 79 | loss: 1.1383

| epoch: 79 | loss: 0.9656

| epoch: 79 | loss: 1.1130

| epoch: 79 | loss: 1.0265

| epoch: 79 | loss: 1.2175

| epoch: 79 | loss: 1.3445

| epoch: 79 | loss: 1.1065

| epoch: 79 | loss: 1.2830

| epoch: 79 | loss: 0.9380

| epoch: 79 | loss: 1.0741

| epoch: 79 | loss: 1.0968

| epoch: 79 | loss: 1.1870

| epoch: 79 | loss: 1.1639

| epoch: 79 | loss: 1.0972

| epoch: 79 | loss: 1.3448

| epoch: 79 | loss: 1.1079

| epoch: 79 | loss: 1.1779

| epoch: 79 | loss: 1.0310

| epoch: 79 | loss: 1.2533

| epoch: 79 | loss: 1.0608

| epoch: 79 | loss: 1.2660

| epoch: 79 | loss: 1.2142

| epoch: 79 | loss: 1.0950

| epoch: 79 | loss: 1.0923

| epoch: 79 | loss: 1.0737

| epoch: 79 | loss: 1.1245

| epoch: 79 | loss: 0.9099

| epoch: 79 | loss: 1.3225

| epoch: 79 | loss: 1.1776

| epoch: 79 | loss: 1.0766

| epoch: 79 | loss: 1.2880

| epoch: 79 | loss: 1.2198

| epoch: 79 | loss: 1.0569

| epoch: 79 | loss: 0.9379

| epoch: 79 | loss: 

KeyboardInterrupt: 

In [ ]:
# #train for keypoint only
# min_loss = 9999

# early_stopping_idx = 0;
# for epoch in range(num_epochs):
#     model.train()
#     val_losses = []
#     losses = []
#     loop = tqdm(train_loader)
#     for i, (images, targets) in enumerate(loop):
#         #grad init
#         optimizer.zero_grad()
#         #forward propagation
#         images = list(image.float().to(device) for image in images)
#         #target
#         targets = [{k: v.to(device) for k, v in t.items()} for t in targets]
#         #calculate loss
#         loss = model(images,targets)['loss_keypoint']
#         losses.append(loss)
#         #back propagation
#         loss.backward()
#         #weight update
#         optimizer.step() 
        
#         if (i+1) % 10 == 0:
#             print(f'| epoch: {epoch} | loss: {loss.item():.4f}')
#             print()
        
#     # validation

#     with torch.no_grad():
#         for k, (val_images, val_targets) in enumerate(val_loader):
#             val_images = list(val_image.float().to(device) for val_image in val_images)
#             val_targets = [{k: v.to(device) for k, v in t.items()} for t in val_targets]
#             val_loss = model(val_images,val_targets)['loss_keypoint']
#             val_losses.append(val_loss)


#     mean_val_loss = sum(val_losses) / len(val_losses)
#     mean_loss = sum(losses) / len(losses)
#     lr = optimizer.param_groups[0]['lr']
#     scheduler.step(mean_loss)
#     writer.add_scalar("Loss/val", mean_val_loss,epoch)
#     writer.add_scalar("Loss/train", mean_loss, epoch)
#     writer.add_scalar("learning_rate", lr, epoch)
#     print(f'| epoch: {epoch} | loss: {mean_loss:.4f} | lr : {lr} | validation loss : {mean_val_loss:.4f}')
#     print()
    
#     if epoch % 10 == 0:
#         torch.save({
#               'epoch': epoch,
#               'model_state_dict': model.state_dict(),
#               'optimizer_state_dict': optimizer.state_dict(),
#               'loss': loss}
#               ,os.path.join(root_dir,f'model_{epoch}.pt'))
    
#     if mean_val_loss < min_loss:
#       early_stopping_idx = 0
#       min_loss = mean_val_loss
#       torch.save({
#               'epoch': epoch,
#               'model_state_dict': model.state_dict(),
#               'optimizer_state_dict': optimizer.state_dict(),
#               'loss': loss}
#               ,os.path.join(root_dir,'best_model.pt'))
#     else:
#         print("Val_loss_increase")
#         early_stopping_idx +=1
#         if early_stopping_idx == 10:
#         print("early stop")
#         #break
# writer.flush()

In [ ]:
sum(cal_loss) / len(cal_loss)

tensor(9.0262, device='cuda:0', grad_fn=<DivBackward0>)

In [ ]:
val_losses

{'loss_box_reg': tensor(0.0006, device='cuda:0', grad_fn=<DivBackward0>),
 'loss_classifier': tensor(0.6977, device='cuda:0', grad_fn=<NllLossBackward>),
 'loss_keypoint': tensor(8.0329, device='cuda:0', grad_fn=<NllLossBackward>),
 'loss_objectness': tensor(0.6896, device='cuda:0', grad_fn=<BinaryCrossEntropyWithLogitsBackward>),
 'loss_rpn_box_reg': tensor(0.1146, device='cuda:0', grad_fn=<DivBackward0>)}

## tensorboard

In [ ]:
writer.close()

In [ ]:
!tensorboard --logdir=runs

Serving TensorBoard on localhost; to expose to the network, use a proxy or pass --bind_all
TensorBoard 2.4.0 at http://localhost:6007/ (Press CTRL+C to quit)


# 6. test

In [ ]:
#추론
model.eval()
all_predictions = []
files = []
with torch.no_grad():
  loop = tqdm(test_loader)
  for filenames, inputs in loop:
    pred = model(inputs.to(device))
    # x means pred[0],pred[1],-----,pred[batch]
    try :
        predictions = [x['keypoints'][0][:,:2].reshape(-1).detach().cpu().numpy() for x in pred]
    except : 
        print(f'filenames : {filenames} | len : {len(pred)}')
    files.extend(filenames)
    for prediction in predictions:
      all_predictions.append(prediction)

  0%|          | 0/800 [00:00<?, ?it/s]

In [ ]:
checkout_pred(1400,all_predictions)

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


# 7. 파일 저장

In [ ]:
all_predictions = np.array(all_predictions)
# for i in range(all_predictions.shape[0]):
#     all_predictions[i, [2*j for j in range(num_classes//2)]] /= 224 / 1920
#     all_predictions[i, [2*j + 1 for j in range(num_classes//2)]] /= 224 / 1080
df_sub = pd.read_csv(os.path.join(root_dir,'data/sample_submission.csv'))
df = pd.DataFrame(columns=df_sub.columns)
df['image'] = files
df.iloc[:, 1:] = all_predictions
print(f'shape : {df.shape}')
df.head()

shape : (1600, 49)


image       nose_x      nose_y   left_eye_x  \
0  730-3-5-36-Z94_B-0000003.jpg   976.406067   330.29776   986.428284   
1  769-3-5-40-Z94_B-0000013.jpg   1104.34668  334.131348  1105.783936   
2  730-3-5-36-Z94_E-0000029.jpg   966.137512  266.925171   963.273926   
3  754-3-5-38-Z94_C-0000001.jpg   991.664612  358.128998   947.040588   
4  737-3-5-37-Z94_A-0000031.jpg  1069.203125  510.017426  1054.849976   

   left_eye_y right_eye_x right_eye_y   left_ear_x  left_ear_y  right_ear_x  \
0  321.650848   977.83783  320.209686   950.634583  301.474731   969.247314   
1  309.638977  1125.90564  309.638977  1115.844727  329.809174  1158.962769   
2  256.850433  973.296387  243.897186   971.864685  245.336441      1016.25   
3  358.128998  994.543579  358.128998   932.645813  358.128998   990.225159   
4  494.186859   1067.7677  494.186859  1031.884766  511.456543  1059.155762   

   ... right_palm_x right_palm_y spine2(back)_x spine2(back)_y  \
0  ...    949.20282   251.034409     944.907593     383.620361   
1  ...  1006.612854   436.423096    1148.901855     447.948944   
2  ...  1043.453979   253.971939    1029.136108     317.298859   
3  ...   990.225159   410.016632     959.995972      477.75882   
4  ...  1192.640381   544.556763    1046.238037     613.635437   

  spine1(waist)_x spine1(waist)_y left_instep_x left_instep_y right_instep_x  \
0       937.74884      444.148712    919.136169    802.995361     890.501221   
1     1150.339111      517.103943   1189.145264    865.760254    1161.837158   
2     1036.295044      379.186523   1069.226074    763.465759      964.70575   
3      959.995972      562.796875    994.543579    938.982178     931.206299   
4     1051.979248      669.761841   1172.545898    895.706665     1125.18042   

  right_instep_y  
0     676.174133  
1     865.760254  
2     760.587219  
3     804.939209  
4     912.976379  

[5 rows x 49 columns]

In [ ]:
from datetime import datetime
now = datetime.now()
timeday = str(now)[5:10]
df.to_csv(os.path.join(root_dir,f'data/submission_{timeday}.csv'), index=False)